<a href="https://colab.research.google.com/github/piesauce/llm-playbooks/blob/ateng%2Fc4_analysis/Chapter2/C4_Dataset_Analysis.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# C4 Dataset Vocabulary Analysis

Using the ‘realnewslike’ subset of C4, prepare a word frequency counter, counting the number of times each word appears in the dataset. To make it simple, define a word as a contiguous sequence of characters separated by white space. Remove frequent function words (called stop words in NLP) like ‘the’, ‘is’ etc from your analysis. What topics seem to be underrepresented or overrepresented in your opinion?

In [1]:
!pip install datasets nltk


     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 69.2/69.2 kB 1.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 480.6/480.6 kB 12.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 7.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 179.3/179.3 kB 10.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.7/1.7 MB 43.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 143.5/143.5 kB 9.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.8/194.8 kB 11.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 274.9/274.9 kB 15.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 129.0/129.0 kB 6.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 231.1/231.1 kB 13.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 344.1/344.1 kB 16.4 MB/s eta 0:00:00
  Attempting uninstall: fsspec
    Found existing installation: fsspec 2024.12.0
    Uninstalling fsspec-2024.12.0:
 

In [2]:
import nltk
from nltk.corpus import stopwords
from collections import Counter
from datasets import load_dataset
import string

nltk.download('stopwords')


[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.


True

In [3]:
def main():
    # Load the 'realnewslike' subset of the C4 dataset
    try:
        dataset = load_dataset('allenai/c4', 'realnewslike', split='train')
    except Exception as e:
        print(f"Error loading dataset: {e}")
        return

    # Initialize stop words
    stop_words = set(stopwords.words('english'))

    # Initialize a counter for word frequencies
    word_counter = Counter()

    # Define a translation table to remove punctuation
    translator = str.maketrans('', '', string.punctuation)

    # Iterate through the dataset and count word frequencies
    for idx, example in enumerate(dataset):
        text = example['text']
        # Remove punctuation
        text = text.translate(translator)
        # Tokenize by whitespace
        words = text.lower().split()
        # Remove stop words
        filtered_words = [word for word in words if word not in stop_words]
        # Update the counter
        word_counter.update(filtered_words)

        # Print progress every 10000 examples
        if (idx + 1) % 10000 == 0:
            print(f"Processed {idx + 1} examples...")

    # Get the top 100 most common words
    top_n = 100
    most_common = word_counter.most_common(top_n)

    # Display the results
    print(f"\nTop {top_n} most frequent words (excluding stop words):")
    for rank, (word, freq) in enumerate(most_common, start=1):
        print(f"{rank}. {word}: {freq}")

    # Analyze topic representation
    analyze_topics(most_common)

def analyze_topics(most_common):
    """
    Provide a basic analysis of overrepresented or underrepresented topics
    based on the most common words.
    """
    # Define some boilerplate categories and associated keywords -- can do this with ML if you want ie LDA topic modeling etc
    # but because i am on google colab free, we will just use a set of predifned words for each topic
    topics = {
        'Politics': ['government', 'president', 'election', 'policy', 'congress'],
        'Economy': ['market', 'economy', 'stock', 'trade', 'investment'],
        'Technology': ['technology', 'software', 'internet', 'device', 'computer'],
        'Health': ['health', 'medical', 'doctor', 'disease', 'hospital'],
        'Entertainment': ['movie', 'music', 'television', 'celebrity', 'show'],
        'Sports': ['game', 'team', 'score', 'player', 'season'],
        'Environment': ['environment', 'climate', 'energy', 'pollution', 'conservation'],
        'Education': ['education', 'school', 'university', 'student', 'teacher'],
        'Science': ['science', 'research', 'study', 'experiment', 'theory'],
        'International': ['country', 'international', 'foreign', 'diplomacy', 'global']
    }

    # Initialize a dictionary to hold topic frequencies
    topic_freq = {topic:0 for topic in topics}

    for word, freq in most_common:
        for topic, keywords in topics.items():
            if word in keywords:
                topic_freq[topic] += freq

    # Determine overrepresented and underrepresented topics
    # For simplicity, we'll define overrepresented as top 3 and underrepresented as bottom 3
    sorted_topics = sorted(topic_freq.items(), key=lambda x: x[1], reverse=True)
    overrepresented = sorted_topics[:3]
    underrepresented = sorted_topics[-3:]

    print("\nTopic Representation Analysis:")
    print("\nOverrepresented Topics:")
    for topic, freq in overrepresented:
        print(f"- {topic}: {freq} mentions")

    print("\nUnderrepresented Topics:")
    for topic, freq in underrepresented:
        print(f"- {topic}: {freq} mentions")

if __name__ == "__main__":
    main()

/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


README.md:   0%|          | 0.00/41.1k [00:00<?, ?B/s]

Resolving data files:   0%|          | 0/1024 [00:00<?, ?it/s]

Resolving data files:   0%|          | 0/512 [00:00<?, ?it/s]

c4-train.00000-of-00512.json.gz:   0%|          | 0.00/30.1M [00:00<?, ?B/s]

...

c4-validation.00000-of-00001.json.gz:   0%|          | 0.00/15.3M [00:00<?, ?B/s]

Generating train split:   0%|          | 0/13799838 [00:00<?, ? examples/s]

Generating validation split:   0%|          | 0/13863 [00:00<?, ? examples/s]

Loading dataset shards:   0%|          | 0/76 [00:00<?, ?it/s]

Processed 10000 examples...
Processed 20000 examples...
Processed 30000 examples...
Processed 40000 examples...
Processed 50000 examples...
Processed 60000 examples...
Processed 70000 examples...
Processed 80000 examples...
Processed 90000 examples...
Processed 100000 examples...
Processed 110000 examples...
Processed 120000 examples...
Processed 130000 examples...
Processed 140000 examples...
Processed 150000 examples...
Processed 160000 examples...
Processed 170000 examples...
Processed 180000 examples...
Processed 190000 examples...
Processed 200000 examples...
Processed 210000 examples...
Processed 220000 examples...
Processed 230000 examples...
Processed 240000 examples...
Processed 250000 examples...
Processed 260000 examples...
Processed 270000 examples...
Processed 280000 examples...
Processed 290000 examples...
Processed 300000 examples...
Processed 310000 examples...
Processed 320000 examples...
Processed 330000 examples...
Processed 340000 examples...
Processed 350000 exampl